Since version, codec and bitrate all seem to have an effect, it is difficult to get a clear 'best case', thus we can also just calculate the correlations for the slices in the dataset for which the sample size allows for this:

In [1]:
from pathlib import Path
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import math
import numpy as np
# Use seaborn style defaults and set the default figure size
sns.set(rc={'figure.figsize':(15, 15)})

from tqdm.notebook import tqdm
tqdm().pandas()

# Define correlations to study
cols = [
    ('acousticness', ('mood_acoustic', 'acoustic')),
    ('danceability', ('danceability', 'danceable')),
    ('energy', ('mood_relaxed', 'not_relaxed')),
    ('instrumentalness', ('voice_instrumental', 'instrumental')),
    ('valence', ('mood_happy', 'happy')),
    ('valence', ('mood_sad', 'not_sad'))
]

def pearsonr_ci(x,y,alpha=0.05):
    ''' calculate Pearson correlation along with the confidence interval using scipy and numpy
    Parameters
    ----------
    x, y : iterable object such as a list or np.array
      Input for correlation calculation
    alpha : float
      Significance level. 0.05 by default
    Returns
    -------
    r : float
      Pearson's correlation coefficient
    pval : float
      The corresponding p value
    lo, hi : float
      The lower and upper bound of confidence intervals
    '''

    r, p = stats.pearsonr(x,y)
    r_z = np.arctanh(r)
    se = 1/np.sqrt(x.size-3)
    z = stats.norm.ppf(1-alpha/2)
    lo_z, hi_z = r_z-z*se, r_z+z*se
    lo, hi = np.tanh((lo_z, hi_z))
    return r, p, lo, hi

def get_correlations(data, columns):
    corrs = {
        'Pearson r': [],
        'p': [],
        'low': [],
        'high': []
    }
    for t in columns:
        print("Spotify: {a}\nAcousticBrainz: {b}".format(a=t[0], b=t[1]))
        pearson_r = pearsonr_ci(data[t[0]], data[t[1]])
        print("pearson r: {r}, p: {p}\n".format(r=pearson_r[0], p=pearson_r[1]))

        corrs['Pearson r'].append(pearson_r[0])
        corrs['p'].append(pearson_r[1])
        corrs['low'].append(pearson_r[2])
        corrs['high'].append(pearson_r[3])
    return corrs


# Load in the acousticbrainz dataset into the variable 'acousticbrainz' (V3 also include build SHA to make sure that software
# version is the same on a commit basis.
acousticbrainz = pd.read_hdf(Path.cwd() / 'datasets' / 'acousticbrainzV3.h5')
spotify = pd.read_hdf(Path.cwd() / 'datasets' / 'spotify.h5')
mapping = pd.read_hdf(Path.cwd() / 'datasets' / 'mapping.h5')

C:\Users\Chris\Miniconda3\envs\thesis\lib\site-packages\tqdm\std.py:658: FutureWarning: The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version
  from pandas import Panel


In [2]:
# First, match the spotify and acousticbrainz datasets
acousticbrainz = acousticbrainz.reset_index().rename(columns={"level_0": "mbid", "level_1": "submission"})
merged = acousticbrainz.merge(mapping, on='mbid').merge(spotify, left_on='spotify', right_on='id')

In [3]:
# Then, group by bitrate version combinations and save the sample sizes
groups = merged.groupby(['bit_rate', 'codec', 'essentia_low', 'essentia_git_sha_low', 'essentia_build_sha_low'])
counts = groups.size().sort_values(ascending=False)

In [5]:
corrs = {}

for name, group in groups:
    print(name)
    print(group)

(0, 'ape', '2.1-beta2', 'v2.1_beta2', '70f2e5ece6736b2c40cc944ad0e695b16b925413')
                                        mbid submission  \
50842   74fe75b8-deff-44b7-9f9a-a7cac6d2ceca          0   
79834   4d0731fb-f5ab-46bd-a32a-2b49827ce1e7          0   
102364  f6c55547-c46b-4ad2-ade4-9d19e13516b4          0   
121044  e702eac5-7b1c-483f-8275-a86b149a19a4          1   
121138  747a09ea-d477-43cc-84f5-5742c9dfacd3          0   
161508  79f52199-7753-4207-b435-0138586c3215          0   

        (danceability, danceable)  (danceability, not_danceable)  \
50842                6.781793e-01                       0.321821   
79834                7.483671e-01                       0.251633   
102364               9.988049e-01                       0.001195   
121044               3.000001e-14                       1.000000   
121138               9.043580e-02                       0.909564   
161508               9.998215e-01                       0.000178   

        (gender, female)  (

[1385 rows x 111 columns]
(0, 'flac', '2.1-beta1', 'v2.1_beta1-6-g5578087', '7f154e5731828a63663f0144680ef47bd640f88b')
                                        mbid submission  \
238     0020d161-12cc-4480-9eda-c477d14e50ad          0   
444     cef905a7-85f9-4220-b482-16a3f9fe1742          0   
575     004baef3-b95f-42fc-9c31-31881e09d23d          0   
1845    00f4eabd-338f-41f7-9437-4b51af67d932          0   
2066    94556c6a-917b-488b-ad3f-be0abe177031          0   
...                                      ...        ...   
258356  fe0f0e93-0798-4272-93e8-a518951f2fc9          0   
258969  ff1191a0-582e-461f-b50d-4bfd9aecf0b5          0   
259182  ff7fd0cf-f170-4fa3-8d74-018384feabc8          1   
259432  ffc912c2-ab00-4df1-b631-bbdf27175faa          0   
259488  ffd56ff1-9b57-4ce5-84f0-3403e755bd13          0   

        (danceability, danceable)  (danceability, not_danceable)  \
238                  2.883664e-02                       0.971163   
444                  1.192672e-01  

[203 rows x 111 columns]
(0, 'flac', '2.1-beta2', 'v2.1_beta2-3-gd5e3a6e', '0a826ad6289770054bb7564d59068f1232327ff9')
                                        mbid submission  \
36672   88897259-36c9-4335-93b8-100d2bcab832          4   
36684   88897259-36c9-4335-93b8-100d2bcab832          4   
36696   88897259-36c9-4335-93b8-100d2bcab832          4   
148542  6c7cab10-0b80-4c62-b428-81d1a11fba44          4   
148553  6c7cab10-0b80-4c62-b428-81d1a11fba44          4   
177762  e28c78ca-7f22-41cb-b76e-ddacaaa5c471          3   
219442  c15809d8-db06-4bbc-9448-d2732b142816          4   
244782  e7c254f5-e6ee-4648-90a0-870d67b7987f          0   
244793  e7c254f5-e6ee-4648-90a0-870d67b7987f          0   
256643  fb504f9f-a7a9-4641-a01e-90228ce2c99e          6   

        (danceability, danceable)  (danceability, not_danceable)  \
36672                3.000001e-14                       1.000000   
36684                3.000001e-14                       1.000000   
36696                3.0000

[1 rows x 111 columns]
(56000, 'mp3', '2.1-beta1', 'v2.1_beta1-28-g21ef5f4', '81dca3489dfd3c4275b86ac4d56d870715677d3f')
                                        mbid submission  \
2488    014c49fe-1bed-448f-ae59-82e62af634d6          0   
21189   9b085b4b-831c-4cf0-b8a3-1c851425e72c          0   
21195   b72a1b9c-5abf-4906-b5ef-c1a28e1267d4          2   
22630   34f92a63-2e42-4a3a-b0b4-28b9db15cd82          0   
22638   34f92a63-2e42-4a3a-b0b4-28b9db15cd82          0   
31045   10c7897e-6c42-4a95-88c2-5f15ebc05b35          0   
33585   1263eef6-8c28-4865-805f-25d1f7ff6b4c          0   
35285   136af069-c2fe-4147-b3af-936706575460          4   
54085   1f4a6738-47f1-48de-89d8-33347ffa433d          1   
55538   2034bcd6-fc69-4183-8a64-8736ce55c08f          2   
55541   e184ad43-9675-4b48-9ed2-ccfba4e43122          1   
71298   734db388-6027-4705-84df-5dc605f0889b          5   
71306   734db388-6027-4705-84df-5dc605f0889b          5   
91064   39053613-aa26-43dc-bede-b074cf6d10b1         

[3 rows x 111 columns]
(64010, 'mp3', '2.1-beta2', 'v2.1_beta2-1-ge3940c0', '2d9f1f26377add8aeb1075a9c2973f962c4f09fd')
                                       mbid submission  \
83727  710d955c-3f27-40bb-ab09-b95d0706212f          0   
83728  710d955c-3f27-40bb-ab09-b95d0706212f          1   
95645  3c8c1f3a-1737-4221-a8ec-2588bdef9206          0   
95646  3c8c1f3a-1737-4221-a8ec-2588bdef9206          1   

       (danceability, danceable)  (danceability, not_danceable)  \
83727                   0.229122                   7.708780e-01   
83728                   0.228966                   7.710340e-01   
95645                   1.000000                   1.000000e-07   
95646                   1.000000                   1.000000e-07   

       (gender, female)  (gender, male)  (genre_dortmund, alternative)  \
83727          0.183236        0.816764                       0.044183   
83728          0.183141        0.816859                       0.044147   
95645          0.260697        

...

[1 rows x 111 columns]
(127832, 'mp3', '2.1-beta1', 'v2.1_beta1-28-g21ef5f4-dirty', 'ca57ba49d9b1854bd80e60cf9ccf267278fb7d6b')
                                        mbid submission  \
157682  7615fc1b-613d-416c-baf6-9e86e4007740          0   

        (danceability, danceable)  (danceability, not_danceable)  \
157682               3.000001e-14                            1.0   

        (gender, female)  (gender, male)  (genre_dortmund, alternative)  \
157682          0.622127        0.377873                       0.001215   

        (genre_dortmund, blues)  (genre_dortmund, electronic)  \
157682                 0.000218                       0.99648   

        (genre_dortmund, folkcountry)  ...  time_signature  acousticness  \
157682                       0.000199  ...               4         0.265   

        danceability  energy  instrumentalness  liveness  loudness  \
157682         0.593   0.854               0.0    0.0759    -4.757   

        speechiness  valence   tempo  
1

[1 rows x 111 columns]
(127911, 'mp3', '2.1-beta2', 'v2.1_beta2-1-ge3940c0', '2d9f1f26377add8aeb1075a9c2973f962c4f09fd')
                                        mbid submission  \
213908  b9480b03-a52f-4064-be24-31aee232e9cb          1   

        (danceability, danceable)  (danceability, not_danceable)  \
213908                   0.009753                       0.990247   

        (gender, female)  (gender, male)  (genre_dortmund, alternative)  \
213908           0.80917         0.19083                       0.376129   

        (genre_dortmund, blues)  (genre_dortmund, electronic)  \
213908                 0.079285                      0.048814   

        (genre_dortmund, folkcountry)  ...  time_signature  acousticness  \
213908                       0.298301  ...               4         0.874   

        danceability  energy  instrumentalness  liveness  loudness  \
213908         0.605   0.325             0.176     0.109    -9.684   

        speechiness  valence    tempo  
213908 

[1 rows x 111 columns]
(127961, 'aac', '2.1-beta1', 'v2.1_beta1-28-g21ef5f4-dirty', 'ca57ba49d9b1854bd80e60cf9ccf267278fb7d6b')
                                       mbid submission  \
72893  ea5d1dbc-3ee2-4844-b3b6-ea82fc948752          1   

       (danceability, danceable)  (danceability, not_danceable)  \
72893               3.000001e-14                            1.0   

       (gender, female)  (gender, male)  (genre_dortmund, alternative)  \
72893          0.622127        0.377873                   3.390087e-08   

       (genre_dortmund, blues)  (genre_dortmund, electronic)  \
72893             3.174132e-08                      0.999996   

       (genre_dortmund, folkcountry)  ...  time_signature  acousticness  \
72893                   7.804265e-07  ...               4         0.104   

       danceability  energy  instrumentalness  liveness  loudness  \
72893         0.291   0.919             0.583     0.128    -7.023   

       speechiness  valence    tempo  
72893       0

[4 rows x 111 columns]
(127989, 'aac', '2.1-beta2', 'v2.1_beta2-2-gbb40004', 'c0e182ba78c2de26e491b7b7a4a2c98c1ed34208')
                                       mbid submission  \
57311  9370473b-08e7-4cfd-b594-9289a3adcfd0          6   
62173  24c8706a-e05b-4e87-9c11-78d75ed88cf3          7   
73622  2c623d93-4e45-4886-86af-a153db6da6b5          5   

       (danceability, danceable)  (danceability, not_danceable)  \
57311                   0.002700                       0.997300   
62173                   0.026315                       0.973685   
73622                   0.000002                       0.999998   

       (gender, female)  (gender, male)  (genre_dortmund, alternative)  \
57311          0.196607        0.803393                       0.397014   
62173          0.016738        0.983262                       0.188138   
73622          0.028489        0.971511                       0.350062   

       (genre_dortmund, blues)  (genre_dortmund, electronic)  \
57311           

KeyboardInterrupt: 